# OsmGt example

## Imports and prepare input parameters

In [1]:
from IPython.display import display

from bokeh.plotting import output_notebook

import geopandas as gpd


output_notebook()


location = "Roanne"


Loading BokehJS ...

## Get POIs

In [2]:
%%time
from osm_network import Pois

pois_session = Pois()
pois_session.from_location(location)
print(pois_session.data[1])


2023-03-30 00:49:45 - Pois            - INFO     : Building OsmFeatureModes.poi Data
2023-03-30 00:49:45 - Pois            - INFO     : Building the query
2023-03-30 00:49:45 - Pois            - INFO     : NominatimApi: Query 200:OK in 0.28 sec.
2023-03-30 00:49:45 - Pois            - INFO     : From Roanne
2023-03-30 00:49:45 - Pois            - INFO     : Building the query
2023-03-30 00:49:45 - Pois            - INFO     : Execute the query
2023-03-30 00:49:46 - Pois            - INFO     : OverpassApi: Query 200:OK in 0.36 sec.
{'amenity': 'place_of_worship', 'denomination': 'catholic', 'name': 'Chapelle Jean Puy', 'religion': 'christian', 'wheelchair': 'yes', 'id': '260720129', 'osm_url': 'https://www.openstreetmap.org/node/260720129', 'topo_uuid': 2, 'geometry': <POINT (4.071 46.038)>}
CPU times: user 531 ms, sys: 140 ms, total: 671 ms
Wall time: 1.04 s


## Get Roads

In [3]:
%%time
from osm_network import Roads

vehicle_session = Roads("vehicle")
vehicle_session.from_location(location)

vehicle_session.additional_nodes = pois_session.data
vehicle_session.build_graph()
roads_data = vehicle_session.data

2023-03-30 00:49:46 - Roads           - INFO     : Building OsmFeatureModes.vehicle Data
2023-03-30 00:49:46 - Roads           - INFO     : Building the query
2023-03-30 00:49:46 - Roads           - INFO     : NominatimApi: Query 200:OK in 0.26 sec.
2023-03-30 00:49:46 - Roads           - INFO     : From Roanne
2023-03-30 00:49:46 - Roads           - INFO     : Building the query
2023-03-30 00:49:46 - Roads           - INFO     : Execute the query
2023-03-30 00:49:47 - Roads           - INFO     : OverpassApi: Query 200:OK in 0.55 sec.
2023-03-30 00:49:47 - Roads           - INFO     : Network cleaning...
2023-03-30 00:49:47 - Roads           - INFO     : Starting: Adding new nodes on the network
2023-03-30 00:49:47 - Roads           - INFO     : Find nearest line for each node
2023-03-30 00:49:48 - Roads           - INFO     : Split line
2023-03-30 00:49:48 - Roads           - INFO     : Starting: Find intersections
2023-03-30 00:49:48 - Roads           - INFO     : Done: Find interse

In [4]:
print(len(roads_data))

8831


In [5]:
# gpd.GeoDataFrame([f.to_dict() for f in roads_data], geometry="geometry", crs=f"epsg:{4326}").to_file('dataframe.gpkg', driver='GPKG', layer='name')

## Display roads and nodes

In [6]:
%%time

from bokeh.plotting import show
import geopandas as gpd
from gdf2bokeh import Gdf2Bokeh

map_session = Gdf2Bokeh(
    "My network map",
    width=800,
    height=600,
    background_map_name="CARTODBPOSITRON"
)

map_session.add_layer_from_geodataframe(
    "Roads",
    gpd.GeoDataFrame([f.to_dict() for f in roads_data], geometry="geometry", crs=f"epsg:{4326}"),
    from_epsg=4326,
    color="black")

map_session.add_layer_from_geodataframe(
    "POIs",
    gpd.GeoDataFrame(pois_session.data, geometry="geometry", crs=f"epsg:{4326}"),
    from_epsg=4326,
    color="blue", size=9)

map_session.add_layers_on_maps()

show(map_session.figure)


CPU times: user 4.15 s, sys: 39.4 ms, total: 4.19 s
Wall time: 4.2 s


## Check topology details

In [7]:
%%time

roads_topo_data = vehicle_session.topology_checker()

map_session = Gdf2Bokeh(
    "My topology network map",
    width=800,
    height=600,
    background_map_name="CARTODBPOSITRON"
)

map_session.add_layer_from_dict_list(
    "Roads unchanged",
    roads_topo_data.lines_unchanged,
    from_epsg=4326,
    color="black")

map_session.add_layer_from_dict_list(
    "Roads added",
    roads_topo_data.lines_added,
    from_epsg=4326,
    color="green")

map_session.add_layer_from_dict_list(
    "Roads split",
    roads_topo_data.lines_split,
    from_epsg=4326,
    color="orange")

map_session.add_layer_from_dict_list(
    "Intersections added",
    roads_topo_data.intersections_added,
    from_epsg=4326,
    color="red")

map_session.add_layer_from_dict_list(
    "POIs added",
    roads_topo_data.nodes_added,
    from_epsg=4326,
    color="blue",
    size=9)

map_session.add_layers_on_maps()

show(map_session.figure)


2023-03-30 00:49:54 - Roads           - INFO     : Topolgoy analysis done


CPU times: user 5.45 s, sys: 15 ms, total: 5.47 s
Wall time: 5.51 s
